In [5]:
 ## Deep Learning Sentiment Analysis
import pandas as pd
import numpy as np
from keras.utils import to_categorical
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from collections import OrderedDict
from keras.models import Sequential, Model
from keras.layers import Embedding, Dropout, Reshape, Activation, Input, Flatten, Dense, RepeatVector, BatchNormalization, LSTM, RepeatVector, MaxPooling1D,GlobalMaxPool1D, Conv1D, GRU, Bidirectional
from keras.layers.merge import Dot
from keras.utils import np_utils
from keras.utils.data_utils import get_file
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import skipgrams
from keras.callbacks import EarlyStopping
from tqdm import tqdm
import tensorflow as tf
import joblib
import os
import requests 
import numpy as np
from pathlib import Path
print('GPU avialible: {}'.format(tf.test.is_gpu_available()))
pd.options.display.width = 500

GPU avialible: True


In [6]:


# Download Cornal Moview revirew data sets
try:
    url = 'http://www.cs.cornell.edu/people/pabo/movie-review-data/review_polarity.tar.gz'
    file_path = 'polarity.tar.gz'
    path = Path(file_path)
    response = requests.get(url)

    # write contents of the download 
    path.write_bytes(response.content)

    # unziped the file create a directory called txt_sentoken
    os.system('tar -xzf {}'.format(file_path))

    
except:
    print('skipping download')
    
    # Note if you don't have tar, you may need to use 7zip or another unzipping tool (windows)
    # set positive and negative directory paths
pos_dir = 'txt_sentoken/pos'
neg_dir = 'txt_sentoken/neg'

    
# define a function to read in text
def read_file_list(file_list):
    for file in file_list:
        with open(file, 'r') as f:
            text = f.readlines()
            text = ' '.join(text)
            yield text
            
# get the list of file paths
pos_files = os.listdir(pos_dir)
neg_files = os.listdir(neg_dir)


# data the working dir to the file paths
pos_files = [pos_dir + '/' + f for f in pos_files if 'cv' in f]
neg_files = [neg_dir + '/' + f for f in neg_files if 'cv' in f]
neg_reviews = list(read_file_list(neg_files))
pos_reviews = list(read_file_list(pos_files))
data = pos_reviews + neg_reviews

# positive 1, negative review 5
labels = np.array([1] * len(pos_reviews) + [0] * len(neg_reviews))

#
print(data[1][:200])
print('label:', labels[1])
print('n_docs {}'.format(len(data)))

skipping download
bruce willis and sixth sense director m . night shyamalan re-team to tell the story of david dunne ( willis ) , a stadium security guard who has been having some problems at home that are affecting hi
label: 1
n_docs 2000


In [7]:
from sklearn.model_selection import train_test_split
docs_train, docs_test, y_train, y_test = train_test_split(data, labels, test_size=0.33, random_state=42)

In [8]:
from sklearn.feature_extraction.text import TfidfVectorizer

max_features = 1000
# fits a vocabulary to encode using TFIDF (Term Frequencty Inversion Document Frequencey)
vectorizer = TfidfVectorizer(max_features=max_features)
vectorizer = vectorizer.fit(docs_train)
 
# transforms text documents int numpy arrays of features     
X_train = vectorizer.transform(docs_train).toarray()
X_test = vectorizer.transform(docs_test).toarray()

X_train.shape, X_test.shape

((1340, 1000), (660, 1000))

In [9]:
from keras.models import Model
from keras.layers import Input, Dense
def get_model():
    inputs = Input(shape=(max_features,),  name='input')
    d = Dense(32, name='hidden_layer')(inputs)
    b = BatchNormalization(name='batch_norm_layer')(d)
    d1 = Dense(1, name='dense_output_layer')(b)
    outputs = Activation('sigmoid', name='output_activation')(d1)
    model = Model(inputs=inputs, outputs=outputs, name='sentimentClassifier')

    model.compile(loss='binary_crossentropy', optimizer='Adam', metrics=['accuracy'])
    return model


model = get_model()
model.summary()

Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
Model: "sentimentClassifier"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input (InputLayer)           (None, 1000)              0         
_________________________________________________________________
hidden_layer (Dense)         (None, 32)                32032     
_________________________________________________________________
batch_norm_layer (BatchNorma (None, 32)                128       
_________________________________________________________________
dense_output_layer (Dense)   (None, 1)                 33        
_________________________________________________________________
output_activation (Activatio (None, 1)                 0         
Total params: 32,193
Trainable params: 32,129
Non-trainable params: 64
_________________________________________________________________


In [10]:
esm = EarlyStopping(patience=2)
model.fit(X_train,y_train, validation_data=((X_test, y_test)), epochs=20)


Train on 1340 samples, validate on 660 samples
Epoch 1/20
1340/1340 [==============================] - 1s 595us/step - loss: 0.5691 - accuracy: 0.7164 - val_loss: 0.6591 - val_accuracy: 0.7864
Epoch 2/20
1340/1340 [==============================] - 0s 145us/step - loss: 0.2932 - accuracy: 0.8910 - val_loss: 0.6365 - val_accuracy: 0.8076
Epoch 3/20
1340/1340 [==============================] - 0s 146us/step - loss: 0.2172 - accuracy: 0.9269 - val_loss: 0.6109 - val_accuracy: 0.8212
Epoch 4/20
1340/1340 [==============================] - 0s 151us/step - loss: 0.1655 - accuracy: 0.9500 - val_loss: 0.5808 - val_accuracy: 0.8227
Epoch 5/20
1340/1340 [==============================] - 0s 158us/step - loss: 0.1342 - accuracy: 0.9634 - val_loss: 0.5457 - val_accuracy: 0.8167
Epoch 6/20
1340/1340 [==============================] - 0s 145us/step - loss: 0.1197 - accuracy: 0.9687 - val_loss: 0.5093 - val_accuracy: 0.8121
Epoch 7/20
1340/1340 [==============================] - 0s 141us/step - loss

In [ ]:
import shap
feature_names = vectorizer.get_feature_names()
explainer = shap.KernelExplainer(model.predict, shap.kmeans(X_train, 5), feature_names = feature_names)
shap_values = explainer.shap_values(X_test, nsamples=20)

/home/matthew/.local/lib/python3.6/site-packages/shap/explainers/kernel.py:555: UserWarning: l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
  "l1_reg=\"auto\" is deprecated and in the next version (v0.29) the behavior will change from a " \
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 2 iterations, i.e. alpha=3.364e-02, with an active set of 2 regressors, and the smallest cholesky pivot element being 2.220e-16. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 3 iterations, i.e. alpha=2.299e-02, with an active set of 3 regressors, and the smallest cholesky pivot element bein

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=3.442e-05, with an active set of 11 regressors, and the smallest cholesky pivot element being 1.490e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=3.440e-05, with an active set of 11 regressors, and the smallest cholesky pivot element being 2.220e-16. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=3.440e-05, with an active set of 11 regressors, and the

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 5 iterations, i.e. alpha=3.358e-02, with an active set of 5 regressors, and the smallest cholesky pivot element being 2.107e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 6 iterations, i.e. alpha=3.279e-02, with an active set of 6 regressors, and the smallest cholesky pivot element being 2.107e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 9 iterations, i.e. alpha=1.761e-02, with an active set of 7 regressors, and the small

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 13 iterations, i.e. alpha=5.986e-05, with an active set of 11 regressors, and the smallest cholesky pivot element being 2.581e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 13 iterations, i.e. alpha=5.946e-05, with an active set of 11 regressors, and the smallest cholesky pivot element being 1.490e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 13 iterations, i.e. alpha=5.917e-05, with an active set of 11 regressors, and the

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.044e-02, with an active set of 11 regressors, and the smallest cholesky pivot element being 2.980e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.043e-02, with an active set of 11 regressors, and the smallest cholesky pivot element being 2.220e-16. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.043e-02, with an active set of 11 regressors, and the

...

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 13 iterations, i.e. alpha=8.006e-04, with an active set of 11 regressors, and the smallest cholesky pivot element being 2.581e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 13 iterations, i.e. alpha=7.343e-04, with an active set of 11 regressors, and the smallest cholesky pivot element being 3.332e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 13 iterations, i.e. alpha=9.451e-05, with an active set of 11 regressors, and the

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 5 iterations, i.e. alpha=3.274e-02, with an active set of 5 regressors, and the smallest cholesky pivot element being 1.054e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 8 iterations, i.e. alpha=2.127e-02, with an active set of 8 regressors, and the smallest cholesky pivot element being 1.490e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 8 iterations, i.e. alpha=2.127e-02, with an active set of 8 regressors, and the small

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.587e-03, with an active set of 11 regressors, and the smallest cholesky pivot element being 2.220e-16. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.491e-03, with an active set of 11 regressors, and the smallest cholesky pivot element being 2.220e-16. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.280e-03, with an active set of 11 regressors, and the

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 8 iterations, i.e. alpha=1.080e-02, with an active set of 8 regressors, and the smallest cholesky pivot element being 1.825e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 8 iterations, i.e. alpha=7.675e-03, with an active set of 8 regressors, and the smallest cholesky pivot element being 2.220e-16. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 9 iterations, i.e. alpha=5.270e-03, with an active set of 9 regressors, and the small

/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.265e-04, with an active set of 11 regressors, and the smallest cholesky pivot element being 2.220e-16. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.265e-04, with an active set of 11 regressors, and the smallest cholesky pivot element being 1.054e-08. Reduce max_iter or increase eps parameters.
  ConvergenceWarning)
/home/matthew/.local/lib/python3.6/site-packages/sklearn/linear_model/least_angle.py:578: ConvergenceWarning: Regressors in active set degenerate. Dropping a regressor, after 11 iterations, i.e. alpha=1.265e-04, with an active set of 11 regressors, and the

In [ ]:
import xgboost as xgb
xgb_model = xgb.XGBClassifier()
xgb_model = xgb_model.fit(X_train, y_train,  eval_set=[(X_test, y_test)], early_stopping_rounds=5)

In [ ]:
xgb_explainer = shap.TreeExplainer(xgb_model)
shap_values_xgb = xgb_explainer.shap_values(X_test)

In [ ]:

shap.summary_plot(shap_values[0], X_test,feature_names = feature_names) 

In [ ]:
%matplotlib inline
shap.summary_plot(shap_values_xgb, X_test,feature_names = feature_names) 

In [ ]:
np.set_printoptions(suppress=True)
test_neg = ['I hated that god awefull movie, no one should ever watch it and the director should be fired and the cast should never work again.  It was terrible']
test_neg_x = vectorizer.transform(test_neg)
print('neural net', model.predict(test_neg_x )[0])

print('xgboost Model', xgb_model.predict_proba(test_neg_x )[:, 1])


In [ ]:
test_neg = ['best ever movie, loved every part of it and it was outstanding in every way, 10 out of ten']
test_neg_x = vectorizer.transform(test_neg)
print('neural net', model.predict(test_neg_x )[0])

print('xgboost Model', xgb_model.predict_proba(test_neg_x )[:, 1])